# Create HF Dataset
Create a huggingface dataset from the word frequencies from Danish Gigaword 
(collected before 2022-22-01).
These word frequencies are from the Danish Gigaword Corpus which are tokenized using
the spacy pipeline for Danish `"da_core_news_lg"` using `spacy>=3.0.0,<3.4.0`.
See the script "word_freq.py" for more details.



## Setup

In [1]:
# !pip install datasets==2.8.0

In [2]:
import json
import os
from pathlib import Path
import pandas as pd
from datasets import Dataset, DatasetInfo, DatasetDict
import numpy as np

/home/kenneth/.Envs/word_freq/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
# mapping from domain to top-level domain
domain_mapping_dict = {
    "retsinformationdk": "Legal",
    "skat": "Legal",
    "retspraksis": "Legal",
    "hest": "Social Media",
    "cc": "Web",
    "adl": "Wiki & Books",
    "botxt": "Other",
    "danavis": "News",
    "dannet": "dannet",
    "depbank": "Other",
    "ep": "Conversation",
    "ft": "Conversation",
    "gutenberg": "Wiki & Books",
    "jvj": "Wiki & Books",
    "naat": "Conversation",
    "opensub": "Conversation",
    "relig": "Wiki & Books",
    "spont": "Conversation",
    "synne": "Other",
    "tv2r": "News",
    "wiki": "Wiki & Books",
    "wikibooks": "Wiki & Books",
    "wikisource": "Wiki & Books",
    "twfv19": "Social Media",
}

# mapping from domain to its long name format
longname_mapping_dict = {
    "retsinformationdk": "retsinformation.dk (Danish legal information)",
    "skat": "Skat (Danish tax authority)",
    "retspraksis": "retspraksis (Danish legal information)",
    "hest": "Hestenettet (Danish debate forum)",
    "cc": "Common Crawl",
    "adl": " Archive for Danish Literature",
    "botxt": "Bornholmsk (Danish dialect)",
    "danavis": "Danish daily newspapers",
    "dannet": "DanNet (Danish WordNet)",
    "depbank": "Danish Dependency Treebank",
    "ep": "European Parliament",
    "ft": "Folketinget (Danish Parliament)",
    "gutenberg": "Gutenberg",
    "jvj": "Johannes V. Jensen (Danish poet)",
    "naat": "NAAT",
    "opensub": "Open Subtitles",
    "relig": "Religious texts",
    "spont": "Spontaneous speech",
    "synne": "Synderjysk (Danish dialect)",
    "tv2r": "TV 2 Radio (Danish news)",
    "wiki": "Wikipedia",
    "wikibooks": "Wikibooks",
    "wikisource": "Wikisource",
    "twfv19": "Twitter Folketingsvalget 2019 (Danish election tweets)",
}


## The Data

In [4]:
path = Path("/data/DAGW/word_freqs")
json_files = [str(path / f) for f in os.listdir(path) if f.endswith(".json")]


with open(json_files[0]) as f:
    data = json.load(f)

# inspect
for i, (k, v) in enumerate(data.items()):
    print(k, v)
    if i > 5:
        break

teder {'NOUN': 1}
i {'ADP': 81002, 'ADV': 708, 'CCONJ': 1, 'PRON': 5, 'X': 2}
Marbæk {'PROPN': 3}
? {'PUNCT': 31558}
ville {'AUX': 9184, 'VERB': 177}
jo {'ADV': 15825, 'SCONJ': 227, 'INTJ': 88}
være {'AUX': 12805, 'VERB': 3773, 'X': 1, 'ADJ': 3, 'NOUN': 1, 'PRON': 1}


In [5]:
def get_subdomain(json_file):
    return json_file.split("/")[-1].split(".")[0].split("_")[1]


domains = set([get_subdomain(json_file) for json_file in json_files])
print(domains)


{'dannet', 'adl', 'hest', 'wiki', 'relig', 'botxt', 'synne', 'depbank', 'cc', 'tv2r', 'opensub', 'twfv19', 'retsinformationdk', 'wikibooks', 'jvj', 'ft', 'gutenberg', 'retspraksis', 'ep', 'skat', 'spont', 'wikisource', 'naat'}


## Create the Datasets
We will here create 4 different datasets:

- `word_frequencies` - Danish word frequencies from Danish Gigaword.
- `by_domain` - word frequencies pr. domain.
- `with_pos ` - word frequencies pr. domain with their part-of-speech tags derived from the spacy pipeline for Danish `"da_core_news_lg"`.
- `normalized` - word frequencies pr. domain normalized by the top-level domain.

> Note: This notebook is not very efficient, it is mainly here for documentation of the process.


In [6]:
def convert_to_dataset_format(json_file):
    with open(json_file) as f:
        data = json.load(f)

    domain_origin = get_subdomain(json_file)
    domain = domain_mapping_dict[domain_origin]

    return [
        {
            "word": word,
            "pos": pos,
            "freq": freq,
            "domain": longname_mapping_dict[domain_origin],
            "domain_short": domain_origin,
            "top_level_domain": domain,
        }
        for word, posdict in data.items()
        for pos, freq in posdict.items()
    ]


# load and convert all dataset
def load_and_convert_gen(n=None):
    for i, json_file in enumerate(json_files[:n]):
        print(f"Loading {json_file} ({i+1}/{len(json_files)})")
        samples = convert_to_dataset_format(json_file)
        for sample in samples:
            yield sample


In [7]:
# add dataset info for each of the datasets
info = DatasetInfo(
    description="Danish word frequencies",
    citation="Derczynski, L., Ciosici, M. R., Baglini, R., Christiansen, M. H., Dalsgaard, J. A., Fusaroli, R., ... & Varab, D. (2021). The Danish Gigaword Corpus. In Proceedings of the 23rd Nordic Conference on Computational Linguistics (NoDaLiDa) (pp. 413-421).",
    homepage="https://huggingface.co/datasets/DDSC/partial-danish-gigaword-no-twitter",
    version="1.0.0",
    license="",
)

In [8]:
# convert to huggingface dataset
dataset = Dataset.from_list(list(load_and_convert_gen()), info=info)


Loading /data/DAGW/word_freqs/wordfreq_hest_11.json (1/294)
Loading /data/DAGW/word_freqs/wordfreq_ep_12.json (2/294)
Loading /data/DAGW/word_freqs/wordfreq_skat_1.json (3/294)
Loading /data/DAGW/word_freqs/wordfreq_wiki_12.json (4/294)
Loading /data/DAGW/word_freqs/wordfreq_adl_2.json (5/294)
Loading /data/DAGW/word_freqs/wordfreq_retsinformationdk_46.json (6/294)
Loading /data/DAGW/word_freqs/wordfreq_cc_24.json (7/294)
Loading /data/DAGW/word_freqs/wordfreq_hest_20.json (8/294)
Loading /data/DAGW/word_freqs/wordfreq_opensub_18.json (9/294)
Loading /data/DAGW/word_freqs/wordfreq_relig_0.json (10/294)
Loading /data/DAGW/word_freqs/wordfreq_retsinformationdk_12.json (11/294)
Loading /data/DAGW/word_freqs/wordfreq_retsinformationdk_59.json (12/294)
Loading /data/DAGW/word_freqs/wordfreq_hest_42.json (13/294)
Loading /data/DAGW/word_freqs/wordfreq_retsinformationdk_22.json (14/294)
Loading /data/DAGW/word_freqs/wordfreq_cc_2.json (15/294)
Loading /data/DAGW/word_freqs/wordfreq_ft_11.json

### Create the word_frequencies dataset

In [28]:
df = dataset.to_pandas()


In [10]:
df

word    pos   freq                             domain  \
0                      teder   NOUN      1  Hestenettet (Danish debate forum)   
1                          i    ADP  81002  Hestenettet (Danish debate forum)   
2                          i    ADV    708  Hestenettet (Danish debate forum)   
3                          i  CCONJ      1  Hestenettet (Danish debate forum)   
4                          i   PRON      5  Hestenettet (Danish debate forum)   
...                      ...    ...    ...                                ...   
51035982        Leverandører   NOUN      1      Archive for Danish Literature   
51035983              halvlé   NOUN      1      Archive for Danish Literature   
51035984          Spejlruder   NOUN      1      Archive for Danish Literature   
51035985  Restavrationssalen  PROPN      1      Archive for Danish Literature   
51035986              Kølere   NOUN      1      Archive for Danish Literature   

         domain_short top_level_domain  
0                hest     Social Media  
1                hest     Social Media  
2                hest     Social Media  
3                hest     Social Media  
4                hest     Social Media  
...               ...              ...  
51035982          adl     Wiki & Books  
51035983          adl     Wiki & Books  
51035984          adl     Wiki & Books  
51035985          adl     Wiki & Books  
51035986          adl     Wiki & Books  

[51035987 rows x 6 columns]

In [11]:
df = df.groupby(["word"]).sum().reset_index()

# recalculate log prob
total_freq = df["freq"].sum()
df["log_prob"] = np.log(df["freq"] / total_freq)
df["log_prob_smoothed"] = np.log((df["freq"] + 1) / (total_freq + len(df)))

/tmp/ipykernel_38251/3531764134.py:1: FutureWarning: The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  df = df.groupby(["word"]).sum().reset_index()


In [12]:
df # inspect

word   freq   log_prob  log_prob_smoothed
0                            11523 -11.557025         -11.566130
1         generalforsamling      1 -20.909125         -20.225169
2                            25873 -10.748170         -10.757323
3                            32510 -10.519822         -10.528983
4                               7 -18.963215         -18.838875
...                      ...    ...        ...                ...
11120014             󱤆Passer      3 -19.810513         -19.532022
11120015            󱤈Rygning     10 -18.606540         -18.520421
11120016                 󾌵󾟛󾟛      1 -20.909125         -20.225169
11120017                   􀁸     24 -17.731071         -17.699441
11120018                   􀍴      3 -19.810513         -19.532022

[11120019 rows x 4 columns]

In [15]:
# save to csv
df.to_csv("danish_word_freqs.csv", index=False)

# load using huggingface datasets
word_frequencies = Dataset.from_csv("danish_word_freqs.csv")

Using custom data configuration default-db8b733866850efe
/home/kenneth/.Envs/word_freq/lib/python3.8/site-packages/datasets/builder.py:712: FutureWarning: 'use_auth_token' was deprecated in version 2.7.1 and will be removed in 3.0.0. Pass `use_auth_token` to the initializer/`load_dataset_builder` instead.
  warnings.warn(


Extracting data files: 100%|██████████| 1/1 [00:00<00:00, 839.70it/s]
Generating train split: 0 examples [00:00, ? examples/s]/home/kenneth/.Envs/word_freq/lib/python3.8/site-packages/datasets/download/streaming_download_manager.py:727: FutureWarning: the 'mangle_dupe_cols' keyword is deprecated and will be removed in a future version. Please take steps to stop the use of 'mangle_dupe_cols'
  return pd.read_csv(xopen(filepath_or_buffer, "rb", use_auth_token=use_auth_token), **kwargs)


Dataset csv downloaded and prepared to /home/kenneth/.cache/huggingface/datasets/csv/default-db8b733866850efe/0.0.0. Subsequent calls will reuse this data.


### Create the by_domain dataset


In [49]:
df = dataset.to_pandas()

In [50]:
df

word    pos   freq                             domain  \
0                      teder   NOUN      1  Hestenettet (Danish debate forum)   
1                          i    ADP  81002  Hestenettet (Danish debate forum)   
2                          i    ADV    708  Hestenettet (Danish debate forum)   
3                          i  CCONJ      1  Hestenettet (Danish debate forum)   
4                          i   PRON      5  Hestenettet (Danish debate forum)   
...                      ...    ...    ...                                ...   
51035982        Leverandører   NOUN      1      Archive for Danish Literature   
51035983              halvlé   NOUN      1      Archive for Danish Literature   
51035984          Spejlruder   NOUN      1      Archive for Danish Literature   
51035985  Restavrationssalen  PROPN      1      Archive for Danish Literature   
51035986              Kølere   NOUN      1      Archive for Danish Literature   

         domain_short top_level_domain  
0                hest     Social Media  
1                hest     Social Media  
2                hest     Social Media  
3                hest     Social Media  
4                hest     Social Media  
...               ...              ...  
51035982          adl     Wiki & Books  
51035983          adl     Wiki & Books  
51035984          adl     Wiki & Books  
51035985          adl     Wiki & Books  
51035986          adl     Wiki & Books  

[51035987 rows x 6 columns]

In [51]:
# hide pandas warnings
pd.options.mode.chained_assignment = None

df = df.groupby(["word", "domain", "domain_short"]).sum().reset_index()

# recalculate log prob
def calc_log_prob_pr_domain(df, domains):
    dfs = []
    for domain in domains:
        print(domain)
        df_domains = df.loc[df["domain_short"] == domain]
        total_freq = df_domains["freq"].sum()
        df_domains["log_prob"] = np.log(df_domains["freq"] / total_freq)
        df_domains["log_prob_smoothed"] = np.log((df_domains["freq"] + 1) / (total_freq + len(df_domains)))
        dfs.append(df_domains)
    
    return pd.concat(dfs)

df = calc_log_prob_pr_domain(df, domains)

/tmp/ipykernel_38251/2877160612.py:4: FutureWarning: The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  df = df.groupby(["word", "domain", "domain_short"]).sum().reset_index()


dannet
adl
hest
wiki
relig
botxt
synne
depbank
cc
tv2r
opensub
twfv19
retsinformationdk
wikibooks
jvj
ft
gutenberg
retspraksis
ep
skat
spont
wikisource
naat


In [52]:
df

word                   domain domain_short  freq   log_prob  \
4486           DanNet (Danish WordNet)       dannet    38  -9.948003   
14344       !  DanNet (Danish WordNet)       dannet   686  -7.054711   
15182       $  DanNet (Danish WordNet)       dannet     2 -12.892442   
15231       %  DanNet (Danish WordNet)       dannet   104  -8.941198   
15272       &  DanNet (Danish WordNet)       dannet    49  -9.693769   
...       ...                      ...          ...   ...        ...   
15308188    ’                     NAAT         naat   123  -7.307371   
15309280    “                     NAAT         naat    47  -8.269408   
15309314    ”                     NAAT         naat   139  -7.185082   
15309694    •                     NAAT         naat     5 -10.510118   
15310402    …                     NAAT         naat    11  -9.721660   

          log_prob_smoothed  
4486             -10.034464  
14344             -7.165691  
15182            -12.599413  
15231             -9.044065  
15272             -9.786003  
...                     ...  
15308188          -7.369814  
15309280          -8.318895  
15309314          -7.248453  
15309694         -10.398336  
15310402          -9.705189  

[15326084 rows x 6 columns]

In [55]:
# save to csv
df.to_csv("danish_word_freqs_by_domain.csv", index=False)

# load using huggingface datasets
by_domain = Dataset.from_csv("danish_word_freqs_by_domain.csv")

Using custom data configuration default-bcdefdf7aa1acd36
/home/kenneth/.Envs/word_freq/lib/python3.8/site-packages/datasets/builder.py:712: FutureWarning: 'use_auth_token' was deprecated in version 2.7.1 and will be removed in 3.0.0. Pass `use_auth_token` to the initializer/`load_dataset_builder` instead.
  warnings.warn(


Extracting data files: 100%|██████████| 1/1 [00:00<00:00, 565.04it/s]
Generating train split: 0 examples [00:00, ? examples/s]/home/kenneth/.Envs/word_freq/lib/python3.8/site-packages/datasets/download/streaming_download_manager.py:727: FutureWarning: the 'mangle_dupe_cols' keyword is deprecated and will be removed in a future version. Please take steps to stop the use of 'mangle_dupe_cols'
  return pd.read_csv(xopen(filepath_or_buffer, "rb", use_auth_token=use_auth_token), **kwargs)


Dataset csv downloaded and prepared to /home/kenneth/.cache/huggingface/datasets/csv/default-bcdefdf7aa1acd36/0.0.0. Subsequent calls will reuse this data.


### Create the with_pos dataset

In [56]:
df = dataset.to_pandas()
df = df.groupby(["word", "domain", "domain_short"]).sum().reset_index()

# calculate without domains log prob
df = calc_log_prob_pr_domain(df, domains)

# inspect
df

/tmp/ipykernel_38251/2868179020.py:2: FutureWarning: The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  df = df.groupby(["word", "domain", "domain_short"]).sum().reset_index()


dannet
adl
hest
wiki
relig
botxt
synne
depbank
cc
tv2r
opensub
twfv19
retsinformationdk
wikibooks
jvj
ft
gutenberg
retspraksis
ep
skat
spont
wikisource
naat


word                   domain domain_short  freq   log_prob  \
4486           DanNet (Danish WordNet)       dannet    38  -9.948003   
14344       !  DanNet (Danish WordNet)       dannet   686  -7.054711   
15182       $  DanNet (Danish WordNet)       dannet     2 -12.892442   
15231       %  DanNet (Danish WordNet)       dannet   104  -8.941198   
15272       &  DanNet (Danish WordNet)       dannet    49  -9.693769   
...       ...                      ...          ...   ...        ...   
15308188    ’                     NAAT         naat   123  -7.307371   
15309280    “                     NAAT         naat    47  -8.269408   
15309314    ”                     NAAT         naat   139  -7.185082   
15309694    •                     NAAT         naat     5 -10.510118   
15310402    …                     NAAT         naat    11  -9.721660   

          log_prob_smoothed  
4486             -10.034464  
14344             -7.165691  
15182            -12.599413  
15231             -9.044065  
15272             -9.786003  
...                     ...  
15308188          -7.369814  
15309280          -8.318895  
15309314          -7.248453  
15309694         -10.398336  
15310402          -9.705189  

[15326084 rows x 6 columns]

In [57]:
# with_pos = Dataset.from_pandas(df, info=info)

# save to csv
df.to_csv("danish_word_freqs_with_pos.csv", index=False)
with_pos = Dataset.from_csv("danish_word_freqs_with_pos.csv")

Using custom data configuration default-21900efb838e4bd8
/home/kenneth/.Envs/word_freq/lib/python3.8/site-packages/datasets/builder.py:712: FutureWarning: 'use_auth_token' was deprecated in version 2.7.1 and will be removed in 3.0.0. Pass `use_auth_token` to the initializer/`load_dataset_builder` instead.
  warnings.warn(


Extracting data files: 100%|██████████| 1/1 [00:00<00:00, 455.46it/s]
Generating train split: 0 examples [00:00, ? examples/s]/home/kenneth/.Envs/word_freq/lib/python3.8/site-packages/datasets/download/streaming_download_manager.py:727: FutureWarning: the 'mangle_dupe_cols' keyword is deprecated and will be removed in a future version. Please take steps to stop the use of 'mangle_dupe_cols'
  return pd.read_csv(xopen(filepath_or_buffer, "rb", use_auth_token=use_auth_token), **kwargs)


Dataset csv downloaded and prepared to /home/kenneth/.cache/huggingface/datasets/csv/default-21900efb838e4bd8/0.0.0. Subsequent calls will reuse this data.


### Create the normalized dataset


In [59]:
df = dataset.to_pandas()
total_freq = df["freq"].sum()
tl_domains = set(df["top_level_domain"])
words_pr_domain = total_freq / len(tl_domains)

df = df.groupby(["word", "top_level_domain"]).sum().reset_index()

dfs = []
for dom in tl_domains:
    print(dom)
    # break
    dom_df = df[df["top_level_domain"] == dom]
    dom_total_freq = dom_df["freq"].sum()
    dom_df["freq"] = dom_df["freq"] * words_pr_domain / dom_total_freq
    assert dom_df["freq"].sum() - words_pr_domain < 1e-5
    dfs.append(dom_df)

df = pd.concat(dfs)
df["log_prob"] = np.log(df["freq"] / total_freq)
df["log_prob_smoothed"] = np.log((df["freq"] + 1) / (total_freq + len(df)))

# check that the total freq is the same
assert df["freq"].sum() - total_freq < 1e-5
# check that the total freq is the same pr domain
print(df.groupby("top_level_domain")["freq"].sum())

# inspect
df

/tmp/ipykernel_38251/710725097.py:6: FutureWarning: The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  df = df.groupby(["word", "top_level_domain"]).sum().reset_index()


Social Media
dannet
Web
News
Legal
Wiki & Books
Conversation
Other
top_level_domain
Conversation    150531583.5
Legal           150531583.5
News            150531583.5
Other           150531583.5
Social Media    150531583.5
Web             150531583.5
Wiki & Books    150531583.5
dannet          150531583.5
Name: freq, dtype: float64


word top_level_domain  \
297                                                      \n     Social Media   
359                                                    \n\n     Social Media   
370                                                \n\n\n\n     Social Media   
507       \n\n\n\n \n \n\n\n \n \n\n\n \n \n\n\n \n \n\n...     Social Media   
508       \n\n\n\n \n \n \n \n \n \n\n\n \n \n \n \n \n ...     Social Media   
...                                                     ...              ...   
13869006                                                  …            Other   
13869011                                                 ……            Other   
13871529                                             ⟨hanj⟩            Other   
13871552                                             ⟩Gånga            Other   
13882710                                               ﻿Goa            Other   

                  freq   log_prob  log_prob_smoothed  
297       1.721349e+06  -6.550506          -6.561969  
359       1.643463e+03 -13.504564         -13.515419  
370       1.148070e+00 -20.771043         -20.156018  
507       5.740351e-01 -21.464190         -20.466946  
508       5.740351e-01 -21.464190         -20.466946  
...                ...        ...                ...  
13869006  1.269625e+04 -11.460063         -11.471448  
13869011  6.925227e+02 -14.368784         -14.378804  
13871529  4.616818e+02 -14.774249         -14.783549  
13871552  2.308409e+02 -15.467396         -15.474537  
13882710  2.308409e+02 -15.467396         -15.474537  

[13884033 rows x 5 columns]

In [60]:
# normalized = Dataset.from_pandas(df, info=info)

# save to csv
df.to_csv("danish_word_freqs_normalized.csv", index=False)
normalized = Dataset.from_csv("danish_word_freqs_normalized.csv")

Using custom data configuration default-dde703a9c875a737
/home/kenneth/.Envs/word_freq/lib/python3.8/site-packages/datasets/builder.py:712: FutureWarning: 'use_auth_token' was deprecated in version 2.7.1 and will be removed in 3.0.0. Pass `use_auth_token` to the initializer/`load_dataset_builder` instead.
  warnings.warn(


Extracting data files: 100%|██████████| 1/1 [00:00<00:00, 569.72it/s]
Generating train split: 0 examples [00:00, ? examples/s]/home/kenneth/.Envs/word_freq/lib/python3.8/site-packages/datasets/download/streaming_download_manager.py:727: FutureWarning: the 'mangle_dupe_cols' keyword is deprecated and will be removed in a future version. Please take steps to stop the use of 'mangle_dupe_cols'
  return pd.read_csv(xopen(filepath_or_buffer, "rb", use_auth_token=use_auth_token), **kwargs)


Dataset csv downloaded and prepared to /home/kenneth/.cache/huggingface/datasets/csv/default-dde703a9c875a737/0.0.0. Subsequent calls will reuse this data.


## Upload to Huggingface Hub

In [61]:
ds_dict = DatasetDict({
    "word_frequencies": word_frequencies,
    "by_domain": by_domain,
    "with_pos": with_pos,
    "normalized": normalized,
})

In [64]:
word_frequencies.push_to_hub("chcaa/dagw-word-frequencies")

Pushing dataset shards to the dataset hub: 100%|██████████| 1/1 [00:18<00:00, 18.75s/it]


In [65]:
by_domain.push_to_hub("chcaa/dagw-word-frequencies-by-domain")

Pushing dataset shards to the dataset hub: 100%|██████████| 3/3 [00:36<00:00, 12.04s/it]


In [66]:
with_pos.push_to_hub("chcaa/dagw-word-frequencies-by-domain-with-pos-tags")

Pushing dataset shards to the dataset hub: 100%|██████████| 3/3 [00:38<00:00, 12.80s/it]


In [67]:
normalized.push_to_hub("chcaa/dagw-word-frequencies-normalized-by-domain")

Pushing dataset shards to the dataset hub: 100%|██████████| 2/2 [00:27<00:00, 13.59s/it]
